---

_You are currently looking at **version 1.1** of this notebook. To download notebooks and datafiles, as well as get help on Jupyter notebooks in the Coursera platform, visit the [Jupyter Notebook FAQ](https://www.coursera.org/learn/python-data-analysis/resources/0dhYG) course resource._

---

In [1]:
import pandas as pd
import numpy as np
from scipy.stats import ttest_ind

# Assignment 4 - Hypothesis Testing
This assignment requires more individual learning than previous assignments - you are encouraged to check out the [pandas documentation](http://pandas.pydata.org/pandas-docs/stable/) to find functions or methods you might not have used yet, or ask questions on [Stack Overflow](http://stackoverflow.com/) and tag them as pandas and python related. And of course, the discussion forums are open for interaction with your peers and the course staff.

Definitions:
* A _quarter_ is a specific three month period, Q1 is January through March, Q2 is April through June, Q3 is July through September, Q4 is October through December.
* A _recession_ is defined as starting with two consecutive quarters of GDP decline, and ending with two consecutive quarters of GDP growth.
* A _recession bottom_ is the quarter within a recession which had the lowest GDP.
* A _university town_ is a city which has a high percentage of university students compared to the total population of the city.

**Hypothesis**: University towns have their mean housing prices less effected by recessions. Run a t-test to compare the ratio of the mean price of houses in university towns the quarter before the recession starts compared to the recession bottom. (`price_ratio=quarter_before_recession/recession_bottom`)

The following data files are available for this assignment:
* From the [Zillow research data site](http://www.zillow.com/research/data/) there is housing data for the United States. In particular the datafile for [all homes at a city level](http://files.zillowstatic.com/research/public/City/City_Zhvi_AllHomes.csv), ```City_Zhvi_AllHomes.csv```, has median home sale prices at a fine grained level.
* From the Wikipedia page on college towns is a list of [university towns in the United States](https://en.wikipedia.org/wiki/List_of_college_towns#College_towns_in_the_United_States) which has been copy and pasted into the file ```university_towns.txt```.
* From Bureau of Economic Analysis, US Department of Commerce, the [GDP over time](http://www.bea.gov/national/index.htm#gdp) of the United States in current dollars (use the chained value in 2009 dollars), in quarterly intervals, in the file ```gdplev.xls```. For this assignment, only look at GDP data from the first quarter of 2000 onward.

Each function in this assignment below is worth 10%, with the exception of ```run_ttest()```, which is worth 50%.

In [2]:
# Use this dictionary to map state names to two letter acronyms
states = {'OH': 'Ohio', 'KY': 'Kentucky', 'AS': 'American Samoa', 'NV': 'Nevada', 'WY': 'Wyoming', 'NA': 'National', 'AL': 'Alabama', 'MD': 'Maryland', 'AK': 'Alaska', 'UT': 'Utah', 'OR': 'Oregon', 'MT': 'Montana', 'IL': 'Illinois', 'TN': 'Tennessee', 'DC': 'District of Columbia', 'VT': 'Vermont', 'ID': 'Idaho', 'AR': 'Arkansas', 'ME': 'Maine', 'WA': 'Washington', 'HI': 'Hawaii', 'WI': 'Wisconsin', 'MI': 'Michigan', 'IN': 'Indiana', 'NJ': 'New Jersey', 'AZ': 'Arizona', 'GU': 'Guam', 'MS': 'Mississippi', 'PR': 'Puerto Rico', 'NC': 'North Carolina', 'TX': 'Texas', 'SD': 'South Dakota', 'MP': 'Northern Mariana Islands', 'IA': 'Iowa', 'MO': 'Missouri', 'CT': 'Connecticut', 'WV': 'West Virginia', 'SC': 'South Carolina', 'LA': 'Louisiana', 'KS': 'Kansas', 'NY': 'New York', 'NE': 'Nebraska', 'OK': 'Oklahoma', 'FL': 'Florida', 'CA': 'California', 'CO': 'Colorado', 'PA': 'Pennsylvania', 'DE': 'Delaware', 'NM': 'New Mexico', 'RI': 'Rhode Island', 'MN': 'Minnesota', 'VI': 'Virgin Islands', 'NH': 'New Hampshire', 'MA': 'Massachusetts', 'GA': 'Georgia', 'ND': 'North Dakota', 'VA': 'Virginia'}

In [3]:
import pandas as pd
import numpy as np
def get_list_of_university_towns():
    '''Returns a DataFrame of towns and the states they are in from the 
    university_towns.txt list. The format of the DataFrame should be:
    DataFrame( [ ["Michigan", "Ann Arbor"], ["Michigan", "Yipsilanti"] ], 
    columns=["State", "RegionName"]  )
    
    The following cleaning needs to be done:

    1. For "State", removing characters from "[" to the end.
    2. For "RegionName", when applicable, removing every character from " (" to the end.
    3. Depending on how you read the data, you may need to remove newline character '\n'. '''

    filename = "university_towns.txt"
    f = open(filename, 'r')
    lines = f.readlines()
    #s1 = pd.Series(states)
    #s2 = pd.DataFrame(s1,columns=['State'])
    #s2['State ID']=s2.index
    #s2 = s2.reset_index(drop=True)
    #s2 = s2.set_index(['State'])
    #print(s2)
    df = pd.DataFrame(columns=['State','RegionName'])
    for il in lines:
        str = il.rstrip('\n')      
        a=str.find('[edit]')
        b=str.find(' (')
        if a!=-1:
            state = str[:a]
            #print(str[:a],a)
        else :
            if b!=-1 :
                city = str[:b]
            else :
                city = str
            df=df.append({
                "State": state,
                "RegionName":  city
                }, ignore_index=True) 
    #df = df.set_index(['State'])
    #df = pd.merge(df, s2, how='outer', left_index=True, right_index=True)
    
    return df
get_list_of_university_towns()

State                    RegionName
0          Alabama                        Auburn
1          Alabama                      Florence
2          Alabama                  Jacksonville
3          Alabama                    Livingston
4          Alabama                    Montevallo
5          Alabama                          Troy
6          Alabama                    Tuscaloosa
7          Alabama                      Tuskegee
8           Alaska                     Fairbanks
9          Arizona                     Flagstaff
10         Arizona                         Tempe
11         Arizona                        Tucson
12        Arkansas                   Arkadelphia
13        Arkansas                        Conway
14        Arkansas                  Fayetteville
15        Arkansas                     Jonesboro
16        Arkansas                      Magnolia
17        Arkansas                    Monticello
18        Arkansas                  Russellville
19        Arkansas                        Searcy
20      California                        Angwin
21      California                        Arcata
22      California                      Berkeley
23      California                         Chico
24      California                     Claremont
25      California                        Cotati
26      California                         Davis
27      California                        Irvine
28      California                    Isla Vista
29      California  University Park, Los Angeles
..             ...                           ...
487       Virginia                          Wise
488       Virginia                    Chesapeake
489     Washington                    Bellingham
490     Washington                        Cheney
491     Washington                    Ellensburg
492     Washington                       Pullman
493     Washington  University District, Seattle
494  West Virginia                        Athens
495  West Virginia                    Buckhannon
496  West Virginia                      Fairmont
497  West Virginia                     Glenville
498  West Virginia                    Huntington
499  West Virginia                    Montgomery
500  West Virginia                    Morgantown
501  West Virginia                 Shepherdstown
502  West Virginia                  West Liberty
503      Wisconsin                      Appleton
504      Wisconsin                    Eau Claire
505      Wisconsin                     Green Bay
506      Wisconsin                     La Crosse
507      Wisconsin                       Madison
508      Wisconsin                     Menomonie
509      Wisconsin                     Milwaukee
510      Wisconsin                       Oshkosh
511      Wisconsin                   Platteville
512      Wisconsin                   River Falls
513      Wisconsin                 Stevens Point
514      Wisconsin                      Waukesha
515      Wisconsin                    Whitewater
516        Wyoming                       Laramie

[517 rows x 2 columns]

In [4]:
import pandas as pd
import numpy as np
def get_gdp():
    df = pd.read_excel('gdplev.xls' ,header=6)
    df = df.drop('Unnamed: 3', 1)
    df = df.drop('Unnamed: 7', 1)
    df = df.drop('Unnamed: 0', 1)
    df = df.drop('Unnamed: 1', 1)
    df = df.drop('Unnamed: 2', 1)
    df=df.rename(columns = {'Unnamed: 4':'Year/Quarter','Unnamed: 5':'GDP','Unnamed: 6':'GDP in 2009'})
    df['GDP Diff'] = df['GDP in 2009'].diff()
    df['gdp_b'] = df.apply(lambda x : 1 if x['GDP Diff']>0 else 0, axis = 1)
    return df
#get_gdp()

In [5]:
import pandas as pd
import numpy as np

def get_seq(df,begin):
    prev = -1
    seq = []
    for ind, v in zip(df['gdp_b'][begin:].index, df['gdp_b'][begin:].values):
        if v == 0:
            if prev == 1 and len(seq) <= 1:
                seq = []
            seq.append(ind)
        elif v == 1:
            if len(seq) >= 2:
                seq.append(ind)
                if prev == 1:
                    break
            else:
                seq = []
        prev = v
    #print(seq)
    return seq

def get_recession_start():
    '''Returns the year and quarter of the recession start time as a 
    string value in a format such as 2005q3'''
    df = get_gdp()
    start = []

    seq = get_seq(df,1)
    a=seq[0]
    b=seq[len(seq)-1]
    b1 = df['Year/Quarter'][a]
    if b1>'2000q1':    
        start.append(a)
    
    while len(seq)>0 :
        seq = get_seq(df,b+1)
        if len(seq)>0 :
            a=seq[0]
            b=seq[len(seq)-1]
            b1 = df['Year/Quarter'][a]
            if b1>'2000q1':    
                start.append(a)
    StartTime =""
    for ip in start:     
        StartTime = StartTime + df['Year/Quarter'][ip]  
    return StartTime
            
get_recession_start()

'2008q3'

In [6]:
import pandas as pd
import numpy as np
def get_recession_end():
    '''Returns the year and quarter of the recession end time as a 
    string value in a format such as 2005q3'''
    df = get_gdp()
    end = []

    seq = get_seq(df,1)
    b=seq[len(seq)-1]
    b1 = df['Year/Quarter'][b]
    if b1>'2000q1':    
        end.append(b)
    
    while len(seq)>0 :
        seq = get_seq(df,b+1)
        if len(seq)>0 :
            b=seq[len(seq)-1]
            b1 = df['Year/Quarter'][b]
            if b1>'2000q1':    
                end.append(b)
    EndTime =""
    for ip in end:
        #print(ip)
        EndTime = EndTime + df['Year/Quarter'][ip]
    return EndTime
get_recession_end()

'2009q4'

In [7]:
import pandas as pd
import numpy as np

def get_recession_bottom():
    '''Returns the year and quarter of the recession bottom time as a 
    string value in a format such as 2005q3'''
    df = get_gdp()
    BottomTime =""
    seq = get_seq(df,1)
    a=seq[0]
    b=seq[len(seq)-1]
    a1 = np.argmin(df['GDP in 2009'][seq])
    b1 = df['Year/Quarter'][seq][a1]
    if b1>'2000q1':
        BottomTime = BottomTime + b1
    while len(seq)>0 :
        seq = get_seq(df,b+1)
        if len(seq)>0 :
            a=seq[0]
            b=seq[len(seq)-1]
            a1 = np.argmin(df['GDP in 2009'][seq])
            b1 = df['Year/Quarter'][seq][a1]
            if b1>'2000q1':
                BottomTime = BottomTime + b1
    return BottomTime
get_recession_bottom()

'2009q2'

In [26]:
#df = pd.read_csv('City_Zhvi_AllHomes.csv')
#print(df)

       RegionID           RegionName State                           Metro  \
0          6181             New York    NY                        New York   
1         12447          Los Angeles    CA  Los Angeles-Long Beach-Anaheim   
2         17426              Chicago    IL                         Chicago   
3         13271         Philadelphia    PA                    Philadelphia   
4         40326              Phoenix    AZ                         Phoenix   
5         18959            Las Vegas    NV                       Las Vegas   
6         54296            San Diego    CA                       San Diego   
7         38128               Dallas    TX               Dallas-Fort Worth   
8         33839             San Jose    CA                        San Jose   
9         25290         Jacksonville    FL                    Jacksonville   
10        20330        San Francisco    CA                   San Francisco   
11        10221               Austin    TX                      

In [30]:
def ave(row):
    ave1 = np.nanmean(row)
    return ave1
def getchannel(startyr,endyr):
    year=[]
    for i in range(startyr,endyr):
        year.append(i)
    
    a1 = ['01','02','03']
    a2 = ['04','05','06']
    a3 = ['07','08','09']
    a4 = ['10','11','12']
    
    quarter = {'q1':a1,'q2':a2,'q3':a3,'q4':a4}
    #print(type(quarter))
    allquarter = {}
    for iy in year:
        for iq in sorted(quarter):
            yq =""
            yq = str(iy)+str(iq)
            iname = []
            for im in quarter[iq]:
                ym =str(iy)+"-"+str(im)
                iname.append(ym)
            iquarter = {yq:iname}
            allquarter.update(iquarter) 
    return allquarter

def getyearmonth(startyr,endyr):
    year=[]
    for i in range(startyr,endyr):
        year.append(i)   
    month = ['01','02','03','04','05','06','07','08','09','10','11','12']

    iname = []
    for iy in year:
        for iq in sorted(month):
            ym =str(iy)+"-"+str(iq)
            iname.append(ym)
    return iname

def convert_housing_data_to_quarters():
    '''Converts the housing data to quarters and returns it as mean 
    values in a dataframe. This dataframe should be a dataframe with
    columns for 2000q1 through 2016q3, and should have a multi-index
    in the shape of ["State","RegionName"].
    
    Note: Quarters are defined in the assignment description, they are
    not arbitrary three month periods.
    
    The resulting dataframe should have 67 columns, and 10,730 rows.
    '''
    df = pd.read_csv('City_Zhvi_AllHomes.csv')
    s1 = pd.Series(states)
    s2 = pd.DataFrame(s1,columns=['State'])
    df = df.set_index(['State'])
    df = pd.merge(df, s2, how='inner', left_index=True, right_index=True)
    
    df = df.drop('RegionID',axis=1)
    df = df.drop('Metro',axis=1)
    df = df.drop('SizeRank',axis=1)
    df = df.drop('CountyName',axis=1)
    df = df.set_index(['State','RegionName'])

    q1 = getchannel(2000,2017)
    del q1['2016q4']
    del q1['2016q3']
    q1.update({'2016q3':['2016-07','2016-08']})
    
    q2 = getyearmonth(1996,2000)   
    for iq in q2:
        if iq in df.columns:
            df = df.drop(iq,axis=1)
            
    for iq in sorted(q1):
        print(iq)
        ave1 = df[q1[iq]].apply(ave,axis=1)
        for id in q1[iq] :
            if id in df.columns:
                df = df.drop(str(id),axis=1)
        df[str(iq)] = ave1   
    return df

q5 = convert_housing_data_to_quarters()

2000q1


/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-pack

2000q2


/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-pack

2000q3


...

2012q2


/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)
/opt/conda/lib/python3.5/site-pack

2012q3


/opt/conda/lib/python3.5/site-packages/numpy/lib/nanfunctions.py:675: RuntimeWarning: Mean of empty slice
  warnings.warn("Mean of empty slice", RuntimeWarning)


2012q4
2013q1
2013q2
2013q3
2013q4
2014q1
2014q2
2014q3
2014q4
2015q1
2015q2
2015q3
2015q4
2016q1
2016q2
2016q3


In [31]:
q5

2000q1         2000q2         2000q3  \
State         RegionName                                                      
Alaska        Anchorage         174633.333333  175266.666667  179566.666667   
              Fairbanks         163200.000000  165033.333333  169300.000000   
              Palmer            168766.666667  170566.666667  174233.333333   
              North Pole        157466.666667  159100.000000  162133.333333   
              Juneau            192466.666667  194300.000000  195166.666667   
              Kenai                       NaN            NaN            NaN   
              Soldotna                    NaN            NaN            NaN   
              Kodiak                      NaN            NaN            NaN   
              Tanaina           160500.000000  163500.000000  166366.666667   
              Ketchikan                   NaN            NaN            NaN   
              Lakes             172733.333333  174133.333333  177266.666667   
              Homer                       NaN            NaN            NaN   
              Seward                      NaN            NaN            NaN   
              Anchor Point                NaN            NaN            NaN   
Alabama       Mobile             78233.333333   79366.666667   80433.333333   
              Birmingham         54033.333333   54400.000000   54966.666667   
              Huntsville                  NaN            NaN            NaN   
              Tuscaloosa        104500.000000  106033.333333  108500.000000   
              Decatur                     NaN            NaN            NaN   
              Hoover            184966.666667  186366.666667  187200.000000   
              Madison                     NaN            NaN            NaN   
              Northport         125866.666667  126366.666667  126633.333333   
              Wetumpka                    NaN            NaN            NaN   
              Fairhope          161400.000000  161933.333333  161633.333333   
              Albertville        73966.666667   72600.000000   72833.333333   
              Alabaster         122133.333333  123066.666667  123166.666667   
              Prichard                    NaN            NaN            NaN   
              Theodore           76900.000000   78300.000000   78066.666667   
              Daphne            123166.666667  120233.333333  122300.000000   
              Homewood          158333.333333  159666.666667  161100.000000   
...                                       ...            ...            ...   
Wisconsin     Holland           151033.333333  150500.000000  153233.333333   
West Virginia Parkersburg        54900.000000   55833.333333   56633.333333   
              Charleston         59533.333333   59366.666667   59366.666667   
              Elkview                     NaN            NaN            NaN   
              South Charleston            NaN            NaN            NaN   
              Vienna             72266.666667   74533.333333   75333.333333   
              Cross Lanes        78133.333333   78066.666667   79233.333333   
              Saint Albans       63833.333333   64700.000000   65200.000000   
              Dunbar                      NaN            NaN            NaN   
              Nitro                       NaN            NaN            NaN   
              Williamstown       82933.333333   85200.000000   86466.666667   
              Clendenin          39966.666667   38200.000000   40500.000000   
              Sissonville        57200.000000   58200.000000   61200.000000   
              Washington         83900.000000   86033.333333   88333.333333   
              Davisville                  NaN            NaN            NaN   
              Mineral Wells      75533.333333   77233.333333   81966.666667   
              Upper Falls        53033.333333   52333.333333   52100.000000   
              Chesapeake                  NaN            NaN            NaN   
          

In [32]:
import re
#q5 = convert_housing_data_to_quarters()
pattern = re.compile("\d\d\d\dq[1-4]")
res = 'Columns type test: '
if type(q5.columns) == pd.indexes.base.Index: 
    res += 'Passed' 
    res += '\nColumns names test: '
    if q5.columns.map(pattern.match).astype(bool).all():
        res += 'Passed'
    else:
        res += 'Failed'
        res += "\n Do the column names look like ['2000q1','2000q2'....]"
        res += '\n PS. column names are case sensitive'
else:
    res +='Failed'
    res += "\n Did you remember to change the column names back "
    res += "to strings in the format e.g. Index(['2000q1', '2000q2',...],dtype='object')"
res += "\nState name test: "    
if set(q5.index.get_level_values(0)).issubset(set(states.values())):
    res += 'Passed' 
else:
    res += 'Failed'
    res += "\n Did you map the abbreviated state names to the full names using the precoded states dictionary"
res += "\nShape test: "
if q5.shape == (10730,67):
    res += 'Passed'
else:
    res += 'Failed'

#generate all column names
columns = set(pd.date_range(
    start="2000", end="2017", freq='Q').map(
    lambda x: "{:}q{:}".format(x.year,x.quarter))[:-1])
res += "\nColumn Names test: "
if set(q5.columns)==columns:
    res += 'Passed'
else:
    res += 'Failed'
    res += "\nmissing columns" + str(columns-set(q5.columns))

print(res)

Columns type test: Passed
Columns names test: Passed
State name test: Passed
Shape test: Passed
Column Names test: Passed


In [64]:
from scipy import stats
def run_ttest():
    '''First creates new data showing the decline or growth of housing prices
    between the recession start and the recession bottom. Then runs a ttest
    comparing the university town values to the non-university towns values, 
    return whether the alternative hypothesis (that the two groups are the same)
    is true or not as well as the p-value of the confidence. 
    
    Return the tuple (different, p, better) where different=True if the t-test is
    True at a p<0.01 (we reject the null hypothesis), or different=False if 
    otherwise (we cannot reject the null hypothesis). The variable p should
    be equal to the exact p value returned from scipy.stats.ttest_ind(). The
    value for better should be either "university town" or "non-university town"
    depending on which has a lower mean price ratio (which is equivilent to a
    reduced market loss).'''
    #hdf = convert_housing_data_to_quarters()
    hdf = q5
    rec_start=get_recession_start()
    rec_bottom = get_recession_bottom()
    ul = get_list_of_university_towns()
    qrt_bfr_rec_start ="2008q2"
    hdf['PriceRatio'] = hdf[qrt_bfr_rec_start].div(hdf[rec_bottom])
    tuple_list = list(zip(ul['State'], ul['RegionName']))
    #convert ul to a list of tuples i.e [(State1,RegionName1),(State2,RegionName2),.....,(State517,RegionName517)]
    university_towns = hdf.loc[tuple_list].dropna()
    non_university_towns = hdf.loc[~hdf.index.isin(tuple_list)].dropna()
    #print(non_university_towns['PriceRatio'])
    d1 = stats.ttest_ind(university_towns['PriceRatio'], non_university_towns['PriceRatio'])
    p = d1.pvalue
    different = True
    better = 'university town'
    if p<0.01:
        different = True
    else :
        different = False
    #print(university_towns['PriceRatio'].mean())
    if university_towns['PriceRatio'].dropna().mean() > non_university_towns['PriceRatio'].mean() :
        better = 'non_university town'
    else :
        better = 'university town'
    a = (different, p, better)
    #print(a)
    return a
run_ttest()

(True, 0.0051398853506440662, 'university town')

In [65]:
# test output type (different, p, better)

res = run_ttest()
print('Type test:', 'Passed' if type(
    res) == tuple else 'Failed')
print('test `better` item type:','Passed' if type(res[0]) == bool or type(res[0]) == np.bool_ else 'Failed' )
print('`p` item type test:', 'Passed' if type(
    res[1]) == np.float64 else 'Failed')
print('`different` item type test:',
      'Passed' if type(res[2]) == str else 'Failed')
print('`different` item spelling test:', 'Passed' if res[2] in [
      "university town", "non-university town"] else 'Failed')

Type test: Passed
test `better` item type: Passed
`p` item type test: Passed
`different` item type test: Passed
`different` item spelling test: Passed
